In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive




# Question1 

In [2]:
import os
import re
import numpy as np
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
nltk.download('wordnet')
nltk.download('punkt')
nltk.download('stopwords')
from nltk.stem import WordNetLemmatizer 
from pathlib import Path
from nltk.tokenize import word_tokenize
import glob
from zipfile import ZipFile
import pickle
import math
import pickle
from sklearn.metrics.pairwise import cosine_similarity

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [3]:
list_files = []
for root, dirs, files in os.walk('/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/Humor'):
    for file in files:
        list_files.append(file)
list_files

['takenote.jok',
 'talebeat.hum',
 'talkbizr.txt',
 'taping.hum',
 'tarot.txt',
 'teens.txt',
 'telecom.q',
 'televisi.hum',
 'televisi.txt',
 'temphell.jok',
 'terbear.txt',
 'termpoem.txt',
 'terms.hum',
 'test.hum',
 'test2.jok',
 'test.jok',
 'testchri.txt',
 'texican.dic',
 'texican.lex',
 'textgrap.hum',
 'tfepisod.hum',
 'tfpoems.hum',
 'thecube.hum',
 'the_math.hel',
 'thermite.ana',
 'tickmoon.hum',
 'timetr.hum',
 'tnd.1',
 'top10.elf',
 'top10.txt',
 'top10st1.txt',
 'top10st2.txt',
 'topten.hum',
 'transp.txt',
 'shorties.jok',
 'shuttleb.hum',
 'shrink.news',
 'signatur.jok',
 'sigs.txt',
 'sinksub.txt',
 'skincat',
 'skippy.hum',
 'skippy.txt',
 'slogans.txt',
 'smackjok.hum',
 'smartass.txt',
 'smiley.txt',
 'smokers.txt',
 'smurf_co.txt',
 'smurfkil.hum',
 'smurfs.cc',
 'puzzle.spo',
 'python_s.ong',
 'q.pun',
 'quack26.txt',
 'quantum.jok',
 'quick.jok',
 'quest.hum',
 'quotes.bug',
 'quotes.jok',
 'quotes.txt',
 'rabbit.txt',
 'racist.net',
 'radiolaf.hum',
 'rapmastr

In [5]:
base_path = "/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/Humor"

In [6]:
# Pre-processing Utilities

def word_tokenize(data):
    nltk_tokens = nltk.word_tokenize(data)
    return nltk_tokens

def lower(data):
    return data.lower() 
   

def stopWords(data):
    stop_words = stopwords.words('english')
    processed_tokens=[]
    for w in data:
        if w not in stop_words:
            processed_tokens.append(w)
    return processed_tokens


def punctuationSymbols(data):
    data_no_punk = [re.sub(r'[^\w\s]', '', word) for word in data]
    return data_no_punk

    


def remove_blanks(data):
    data = [x for x in data if x!=' ' and x!='']
    return data

In [7]:
def preprocess(data):    
    data_lower=lower(data)
    data_tokens=word_tokenize(data_lower)
    data_stop_words_no=stopWords(data_tokens) 
    data_punc=punctuationSymbols(data_stop_words_no)
    data_no_blanks = remove_blanks(data_punc)
    data_final = data_no_blanks
    print("Pre-Processing Complete")
    return data_final

In [8]:
'''
Uncomment Cell if no Pickle File
'''


# counter = 0

# docs = []
# for file_name in list_files:
#     try:
#         file = open(base_path+ "/" +file_name, 'r', encoding='cp1250',errors='ignore')
#         text = file.read().replace('\n', ' ')
#         file.close()
#         row = []
#         row.append(counter)
#         counter+=1
#         row.append(file_name)
#         row.append(preprocess(text))
#         docs.append(row)
#     except Exception as e:
#         print(e,file_name)

# docs_df = pd.DataFrame(docs)
# docs_df.to_pickle("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/docs_df.pkl")
# docs_df

'\nUncomment Cell if no Pickle File\n'

In [10]:
docs_df = pickle.load(open('/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/Humor/docs_df.pkl','rb'))
docs_df

0             1                                                  2
0        0     teens.txt  [survive, terrible, teens, owners, guide, q, r...
1        1     stone.hum  [five, persons, gerald, baxter, s, hospital, r...
2        2     staff.txt  [staff, development, response, staff, developm...
3        3     test2.jok  [morgan, csc32deccom, fri, dec, 15, 175227, 19...
4        4  temphell.jok  [temperature, heaven, rather, accurately, comp...
...    ...           ...                                                ...
1128  1128  supermar.rul  [supermarket, shelf, control, dept, re, consum...
1129  1129    spider.hum  [make, tarantula, bite, leg, young, wellfledge...
1130  1130  spoonlis.txt  [newsgroups, altquotations, noel, regtriumfca,...
1131  1131   texican.lex  [wichers, husc7harvardedu, sat, jul, 28, 22165...
1132  1132   steroid.txt  [announcing, discovery, text, file, steroids, ...

[1133 rows x 3 columns]

In [11]:
# Create the Posting
doc_id=0
positional_posting={}  #Key is a Term, Value is dictionary of {docId: positions of that word}
for index,row in docs_df.iterrows():
    
    position=0 #to track position of word within a document
    #TOOD: strip the words in docs
    for word in row.loc[2]:
        word=word.strip()
        # Add each word as an entry to the posting if not already exists
        if word not in positional_posting.keys():
            term = {}
            term.update({doc_id:[position,]})
            positional_posting[word]=term
        else:
            #if word present in positional posting
            if doc_id not in positional_posting[word].keys():
                positional_posting[word].update({doc_id:[position,]})
            else:
                positional_posting[word][doc_id].append(position)    
        position+=1
    doc_id+=1

In [12]:
positional_posting

{'survive': {0: [0],
  12: [91],
  62: [3909, 4952],
  109: [888],
  127: [96],
  147: [2122],
  161: [3086],
  168: [825],
  204: [117],
  263: [1808],
  330: [6739, 18577],
  369: [455],
  379: [515],
  385: [749],
  413: [5986],
  440: [2423],
  478: [361],
  547: [373, 379],
  565: [159, 658],
  568: [98],
  571: [4935, 21403],
  587: [1777, 3634, 4416],
  692: [600],
  711: [325],
  805: [1515],
  824: [3108, 6224],
  827: [586],
  852: [89],
  864: [89],
  869: [1501, 2349],
  870: [182, 236],
  974: [418],
  993: [533],
  1009: [3034],
  1012: [4728],
  1023: [402],
  1052: [1428]},
 'terrible': {0: [1],
  19: [30],
  31: [1971, 2499],
  38: [523],
  51: [691],
  61: [134],
  116: [888],
  127: [356],
  136: [5622],
  153: [23],
  160: [537, 544, 551],
  162: [1014],
  203: [10, 14],
  225: [504],
  263: [2007],
  278: [2935],
  287: [310],
  330: [12518],
  342: [1726],
  381: [284],
  384: [1370],
  390: [416],
  399: [628],
  413: [336, 2646, 4632, 6150],
  428: [612],
  431:

In [13]:
def search_documents(positional_posting,query):
    '''
        Input: i) Positional Posting ii) Query
        Returns: List of Names of Documents that Match the Query
    '''
    if len(query)<1:
        print("INVALID QUERY")
        return None
    
    word=query[0]
    i=1
    solution = positional_posting[word][1]
    while(i<len(query)):
        word=query[i]
        solvent = positional_posting[word][1]
        
        # Find and keep only those documents in which both consequent words occur
        common_docs = []
        for k in solution.keys():
            if k in solvent.keys():
                common_docs.append(k)
        updated_solution={}
        for key in common_docs:
            updated_solution[key]=solution[key]
        solution=updated_solution
        # If no document is left, then quit
        if len(solution)<=0:
            print("NO DOCUMENTS!!!")
            return None
        
        # Keep only those indices, which are consecutive for the two consecutive words
        for doc in solution.keys():
            print("DEBUG 1")
            # check for each possible(common) doucment
            primary_positions=solution[doc]
            secondary_position=solution[doc]
            possible_position=[]
            for position in primary_positions:
                if position+i in secondary_position:
                    possible_position.append(position)
            solution[doc]=possible_position
        i+=1
        
    # GET THE FILE NAMES FROM DOC_ID
    documents_found = []
    for doc_id in solution.keys():
        documents_found.append(docs_df.iloc[doc_id].loc[1])
    return documents_found

### **Query**

In [16]:
query="survive terrible"
query = preprocess(input('Enter Input Query:\t'))
print(query)
# onion white sauce pasta pizza

Enter Input Query:	onion white sauce pasta pizza
Pre-Processing Complete
['onion', 'white', 'sauce', 'pasta', 'pizza']


Make Query Vector


In [ ]:
query_dict = dict.fromkeys(term_document_count_df.index,0)
for q in query: 
  query_dict[q]+=1
query_dict

In [ ]:
query_vector = list(query_dict.values())
query_vector

### **Jaccard Coefficient**

In [ ]:
jaccard = docs_df.copy()
jaccard_scores = []
for doc in docs_df[2]:
  num = len(set(query).intersection(set(doc)))
  denom = len(set(query).union(set(doc)))
  jacc_score = num/denom
  jaccard_scores.append(jacc_score)
jaccard['scores']=jaccard_scores
jaccard = jaccard.sort_values(by='scores',ascending=False)
jaccard['document']=jaccard[1]
jaccard = jaccard.filter(['scores','document'],axis=1)
jaccard.head(10)

scores      document
783  0.038462  strattma.txt
643  0.027523  blkbnsrc.vgn
732  0.027397  oranchic.pol
756  0.021277  pasta001.sal
706  0.019417  egglentl.vgn
969  0.019231  garlpast.vgn
702  0.018692  jawgumbo.fis
749  0.018182    recipe.007
746  0.018018    margos.txt
771  0.017241   venison.txt

### **TF-IDF**

In [19]:
listv = positional_posting.keys()

In [20]:
listv #vocab

dict_keys(['survive', 'terrible', 'teens', 'owners', 'guide', 'q', 'recognize', 'adolescent', 'tell', 'much', 'way', 'looks', 'slams', 'door', 'face', 'said', 'something', 'offensive', 'hello', 'gone', 'awry', 'let', 'count', 'ways', 'one', 'thing', 'eats', '12', 'meals', 'day', 'stead', '3', 'acquired', 'eating', 'habits', 'giant', 'termite', 'continues', 'grow', 'present', 'rate', 'body', 'proportion', 'mouth', 'another', 'longer', 'requires', 'sleep', 'go', 'bed', '4', 'get', '7', 'grouchier', 'usual', 'also', 'intelligence', 'grown', 'point', 'knows', 'everything', 'including', 'say', 'perhaps', 'important', 'talks', 'parents', 'annoying', 'creatures', 'planet', 'stress', 'put', 'earth', 'pester', 'us', 'sure', 'certainty', 'tremendous', 'source', 'embarrassment', 'threats', 'smacking', 'cutting', 'allowance', 'serve', 'make', 'angrier', 'thinks', 'stupid', 'enough', 'changed', 'polite', 'well', 'mannered', 'bleches', 'public', 'responds', 'questions', 'terse', 'phrases', 'leave', 

In [21]:
len(listv)

83288

In [22]:
def text_file(text,file):

  di = {}
  for word in text:
    if word in di:
      di[word] += 1
    else:
      di[word] = 1
  dict_files[file] = di      

In [ ]:
dict_files = {}

for file_name in list_files:
  file = open(base_path+ "/" +file_name, 'r', encoding='cp1250',errors='ignore')
  text = file.read().replace('\n', ' ')
  preprocessed_text = preprocess(text)
  file.close()
  text_file(preprocessed_text,file_name)

Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing Complete
Pre-Processing C

In [ ]:
dict_files

In [ ]:
listv = list(listv)

In [ ]:
list_files

['teens.txt',
 'stone.hum',
 'staff.txt',
 'test2.jok',
 'temphell.jok',
 'spydust.hum',
 'telecom.q',
 'sysadmin.txt',
 'talkbizr.txt',
 'swearfrn.hum',
 'test.jok',
 'stereo.txt',
 'takenote.jok',
 'termpoem.txt',
 'testchri.txt',
 'televisi.hum',
 'taping.hum',
 'talebeat.hum',
 'sungenu.hum',
 'standard.hum',
 'strine.txt',
 'squids.gph',
 'startrek.txt',
 'sysman.txt',
 'test.hum',
 'st_silic.txt',
 'terbear.txt',
 'sigs.txt',
 'smurfs.cc',
 'skippy.hum',
 'q.pun',
 'quest.hum',
 'tnd.1',
 'tfpoems.hum',
 'shrink.news',
 'smokers.txt',
 'quick.jok',
 'python_s.ong',
 'smackjok.hum',
 'quotes.bug',
 'puzzle.spo',
 'topten.hum',
 'quotes.txt',
 'transp.txt',
 'the_math.hel',
 'top10.txt',
 'tfepisod.hum',
 'tickmoon.hum',
 'thermite.ana',
 'top10st1.txt',
 'sinksub.txt',
 'quotes.jok',
 'smurf_co.txt',
 'smiley.txt',
 'signatur.jok',
 'smartass.txt',
 'skincat',
 'shorties.jok',
 'thecube.hum',
 'smurfkil.hum',
 'timetr.hum',
 'shuttleb.hum',
 'quack26.txt',
 'top10st2.txt',
 'sloga

In [ ]:
docs_df[1]

0          teens.txt
1          stone.hum
2          staff.txt
3          test2.jok
4       temphell.jok
            ...     
1128    supermar.rul
1129      spider.hum
1130    spoonlis.txt
1131     texican.lex
1132     steroid.txt
Name: 1, Length: 1133, dtype: object

In [ ]:
dict_file_nums = dict(zip(docs_df[0],docs_df[1]))
dict_file_nums

{0: 'teens.txt',
 1: 'stone.hum',
 2: 'staff.txt',
 3: 'test2.jok',
 4: 'temphell.jok',
 5: 'spydust.hum',
 6: 'telecom.q',
 7: 'sysadmin.txt',
 8: 'talkbizr.txt',
 9: 'swearfrn.hum',
 10: 'test.jok',
 11: 'stereo.txt',
 12: 'takenote.jok',
 13: 'termpoem.txt',
 14: 'testchri.txt',
 15: 'televisi.hum',
 16: 'taping.hum',
 17: 'talebeat.hum',
 18: 'sungenu.hum',
 19: 'standard.hum',
 20: 'strine.txt',
 21: 'squids.gph',
 22: 'startrek.txt',
 23: 'sysman.txt',
 24: 'test.hum',
 25: 'st_silic.txt',
 26: 'terbear.txt',
 27: 'sigs.txt',
 28: 'smurfs.cc',
 29: 'skippy.hum',
 30: 'q.pun',
 31: 'quest.hum',
 32: 'tnd.1',
 33: 'tfpoems.hum',
 34: 'shrink.news',
 35: 'smokers.txt',
 36: 'quick.jok',
 37: 'python_s.ong',
 38: 'smackjok.hum',
 39: 'quotes.bug',
 40: 'puzzle.spo',
 41: 'topten.hum',
 42: 'quotes.txt',
 43: 'transp.txt',
 44: 'the_math.hel',
 45: 'top10.txt',
 46: 'tfepisod.hum',
 47: 'tickmoon.hum',
 48: 'thermite.ana',
 49: 'top10st1.txt',
 50: 'sinksub.txt',
 51: 'quotes.jok',
 5

In [ ]:
def idf(total_docs, word_freq):
  idf_val = np.log(total_docs/word_freq)
  return (idf_val)

In [ ]:
listv[1]

'terrible'

In [ ]:
term_document_count_np=np.zeros((len(listv),len(list_files))) # numpy array of vocab no. of rows and doc no. of columns
term_document_count_df = pd.DataFrame(term_document_count_np,columns=list_files,index=listv)
term_document_count_df

teens.txt  stone.hum  staff.txt  test2.jok  temphell.jok  \
survive         0.0        0.0        0.0        0.0           0.0   
terrible        0.0        0.0        0.0        0.0           0.0   
teens           0.0        0.0        0.0        0.0           0.0   
owners          0.0        0.0        0.0        0.0           0.0   
guide           0.0        0.0        0.0        0.0           0.0   
...             ...        ...        ...        ...           ...   
łáşëúí          0.0        0.0        0.0        0.0           0.0   
iböc            0.0        0.0        0.0        0.0           0.0   
edlin           0.0        0.0        0.0        0.0           0.0   
controlz        0.0        0.0        0.0        0.0           0.0   
seeya           0.0        0.0        0.0        0.0           0.0   

          spydust.hum  telecom.q  sysadmin.txt  talkbizr.txt  swearfrn.hum  \
survive           0.0        0.0           0.0           0.0           0.0   
terrible          0.0        0.0           0.0           0.0           0.0   
teens             0.0        0.0           0.0           0.0           0.0   
owners            0.0        0.0           0.0           0.0           0.0   
guide             0.0        0.0           0.0           0.0           0.0   
...               ...        ...           ...           ...           ...   
łáşëúí            0.0        0.0           0.0           0.0           0.0   
iböc              0.0        0.0           0.0           0.0           0.0   
edlin             0.0        0.0           0.0           0.0           0.0   
controlz          0.0        0.0           0.0           0.0           0.0   
seeya             0.0        0.0           0.0           0.0           0.0   

          ...  strsdiet.txt  terms.hum  suicide2.txt  subrdead.hum  t-10.hum  \
survive   ...           0.0        0.0           0.0           0.0       0.0   
terrible  ...           0.0        0.0           0.0           0.0       0.0   
teens     ...           0.0        0.0           0.0           0.0       0.0   
owners    ...           0.0        0.0           0.0           0.0       0.0   
guide     ...           0.0        0.0           0.0           0.0       0.0   
...       ...           ...        ...           ...           ...       ...   
łáşëúí    ...           0.0        0.0           0.0           0.0       0.0   
iböc      ...           0.0        0.0           0.0           0.0       0.0   
edlin     ...           0.0        0.0           0.0           0.0       0.0   
controlz  ...           0.0        0.0           0.0           0.0       0.0   
seeya     ...           0.0        0.0           0.0           0.0       0.0   

          supermar.rul  spider.hum  spoonlis.txt  texican.lex  steroid.txt  
survive            0.0         0.0           0.0          0.0          0.0  
terrible           0.0         0.0           0.0          0.0          0.0  
teens              0.0         0.0           0.0          0.0          0.0  
owners             0.0         0.0           0.0          0.0          0.0  
guide              0.0         0.0           0.0          0.0          0.0  
...                ...         ...           ...          ...          ...  
łáşëúí             0.0         0.0           0.0          0.0          0.0  
iböc               0.0         0.0           0.0          0.0          0.0  
edlin              0.0         0.0           0.0          0.0          0.0  
controlz           0.0         0.0           0.0          0.0          0.0  
seeya              0.0         0.0           0.0          0.0          0.0  

[83288 rows x 1133 columns]

In [ ]:
'''
Uncomment Cell if no Pickle File
'''


# print("Progress Update:\n")
# i=1
# for file_title, file_term_freq in dict_files.items():
#   for word, frequ in file_term_freq.items():
#     term_document_count_df[file_title][word]=frequ
#     # term_document_count_processed_df[file_title][word]=(1+math.log(frequ,10)) # log normalization
#   print("Documents Processed:\t",i)
#   i+=1
# term_document_count_df

'\nUncomment Cell if no Pickle File\n'

In [ ]:
'''
Uncomment Cell if no Pickle File
'''


# print("Progress Update:\n")
# prog=1
# counts=[]
# for i in range(term_document_count_df.shape[0]):
#   c = (term_document_count_df.iloc[i] > 0).sum()
#   print(c)
#   counts.append(c)
#   print("Words Processed:\t",prog)
#   prog+=1
# counts   # no. of columns for each row that have value greater than 0

'\nUncomment Cell if no Pickle File\n'

In [ ]:
'''
Uncomment Cell if no Pickle File
'''

# term_document_count_df['df']=counts 
# term_document_count_df

'\nUncomment Cell if no Pickle File\n'

In [ ]:
'''
Uncomment Cell if no Pickle File
'''

# total_docs = len(term_document_count_df.columns)
# idf=[]
# for doc_freq in term_document_count_df['df']:
#   idf_term=math.log((total_docs/doc_freq+1),10)
#   idf.append(idf_term)
# idf


'\nUncomment Cell if no Pickle File\n'

In [ ]:
'''
Uncomment Cell if no Pickle File
'''

# term_document_count_df['idf']=idf 
# term_document_count_df

'\nUncomment Cell if no Pickle File\n'

In [ ]:
'''
Uncomment Cell if no Pickle File
'''

# pickle.dump(term_document_count_df, open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/term_document_count_df.pkl", "wb"))

'\nUncomment Cell if no Pickle File\n'

In [ ]:
term_document_count_df = pickle.load(open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/Humor/Copy of term_document_count_df.pkl", "rb"))
term_document_count_df

In [ ]:
def log_normalization(tf):
  if tf==0:
    return 0
  else:
    return 1+math.log(tf,10)

In [ ]:
'''
Uncomment Cell if no Pickle File
'''

# print("Progress Update:\n")
# i=1
# term_document_count_log_normalization_df = pd.DataFrame()
# for doc in dict_file_nums.values():
#   term_document_count_log_normalization_df[doc] = term_document_count_df[doc].apply(log_normalization)
#   print("Documents Processed:\t",i)
#   i+=1
# term_document_count_log_normalization_df

In [ ]:
'''
Uncomment Cell if no Pickle File
'''


# pickle.dump(term_document_count_log_normalization_df, open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/term_document_count_log_normalization_df.pkl", "wb"))

In [ ]:
term_document_count_log_normalization_df = pickle.load(open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/Humor/Copy of term_document_count_log_normalization_df.pkl", "rb"))
term_document_count_log_normalization_df

In [ ]:
def binary(tf):
  if tf>0:
    return 1
  else:
    return 0

In [ ]:
'''
Uncomment Cell if no Pickle File
'''


# print("Progress Update:\n")
# i=1
# term_document_count_binary_df = pd.DataFrame()
# for doc in dict_file_nums.values():
#   term_document_count_binary_df[doc] = term_document_count_df[doc].apply(binary)
#   print("Documents Processed:\t",i)
#   i+=1
# term_document_count_binary_df

In [ ]:
'''
Uncomment Cell if no Pickle File
'''



# pickle.dump(term_document_count_binary_df, open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/term_document_count_binary_df.pkl", "wb"))

In [ ]:
term_document_count_binary_df = pickle.load(open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/Humor/Copy of term_document_count_binary_df.pkl", "rb"))
term_document_count_binary_df

In [ ]:
def term_frequency(tf):
  if sum_tf>0:
    return tf/sum_tf
  else:
    return 0

In [ ]:
'''
Uncomment Cell if no Pickle File
'''



# print("Progress Update:\n")
# i=1
# sum_tf=None
# term_document_count_term_frequency_df = pd.DataFrame()
# for doc in dict_file_nums.values():
#   sum_tf = term_document_count_df[doc].sum()
#   term_document_count_term_frequency_df[doc] = term_document_count_df[doc].apply(term_frequency)
#   print("Documents Processed:\t",i)
#   i+=1
# term_document_count_term_frequency_df

In [ ]:
'''
Uncomment Cell if no Pickle File
'''


# pickle.dump(term_document_count_term_frequency_df, open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/term_document_count_term_frequency_df.pkl", "wb"))

In [ ]:
term_document_count_term_frequency_df = pickle.load(open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/Humor/Copy of term_document_count_term_frequency_df.pkl", "rb"))
term_document_count_term_frequency_df

In [ ]:
def double_normalization(tf):
  if max_tf>0:
    return 0.5+((0.5*tf)/max_tf)
  else:
    return 0.5

In [ ]:
'''
Uncomment Cell if no Pickle File
'''


# print("Progress Update:\n")
# i=1
# term_document_count_double_normalization_df = pd.DataFrame()
# max_tf=None
# for doc in dict_file_nums.values():
#   max_tf = term_document_count_df[doc].sum()
#   term_document_count_double_normalization_df[doc] = term_document_count_df[doc].apply(double_normalization)
#   print("Documents Processed:\t",i)
#   i+=1
# term_document_count_double_normalization_df

In [ ]:
'''
Uncomment Cell if no Pickle File
'''


# pickle.dump(term_document_count_double_normalization_df, open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/term_document_count_double_normalization_df.pkl", "wb"))

In [ ]:
term_document_count_double_normalization_df = pickle.load(open("/content/drive/MyDrive/Humor,Hist,Media,Food.zip (Unzipped Files)/Humor/Copy of term_document_count_double_normalization_df.pkl", "rb"))
term_document_count_double_normalization_df

In [ ]:
def tf_idf_score(query,tf_data,doc_name):
  '''
    Description
  '''
  # print("query",query)
  # print("document",document)
  score=0
  common_terms = [] #ensures to avoid any term in query that is not in the vocab
  if len(query)>1:
    # if more than one word, other wise on for loop, it will iterate over each  character
    for word in query:
      if word in term_document_count_df.index:
        common_terms.append(word)
  else:
    common_terms.append(query)
  tf_data = list(tf_data.loc[ common_terms , doc_name ])
  idf_vals = list(term_document_count_df.loc[common_terms,'idf'])
  for i in range(len(tf_data)):
    term_tf_idf= tf_data[i]*idf_vals[i] #tf*idf # last index is tf-idf
    score+=term_tf_idf
  return score 

Binary

In [ ]:
tf_idf_scores_query = {}
for doc in dict_file_nums.values():
  sc = tf_idf_score(query,term_document_count_binary_df,doc)
  tf_idf_scores_query[doc]=sc
tf_idf_scores_query_sorted = sorted(tf_idf_scores_query.items(), key=lambda x: x[1], reverse=True)
print("Documents Matched using Binary:\n")
tf_idf_scores_query_sorted[:10]

Documents Matched using Binary:



[('appetiz.rcp', 6.5005332292031905),
 ('penndtch', 5.1876849673619105),
 ('vegan.rcp', 5.1876849673619105),
 ('top10.txt', 5.158110548380985),
 ('bread.rcp', 4.586719376819474),
 ('blkbnsrc.vgn', 4.46907174776006),
 ('onetoone.hum', 3.9452753338268476),
 ('foodtips', 3.868106157217623),
 ('insult.lst', 3.3738841622653375),
 ('consp.txt', 3.273871114978194)]

Raw Count

In [ ]:
tf_idf_scores_query = {}
for doc in dict_file_nums.values():
  sc = tf_idf_score(query,term_document_count_df,doc)
  tf_idf_scores_query[doc]=sc
tf_idf_scores_query_sorted = sorted(tf_idf_scores_query.items(), key=lambda x: x[1], reverse=True)
print("Documents Matched using Raw Count:\n")
tf_idf_scores_query_sorted[:10]

Documents Matched using Raw Count:



[('appetiz.rcp', 123.51679195931202),
 ('vegan.rcp', 111.28152322826028),
 ('candy.txt', 78.64411125255762),
 ('penndtch', 75.78468496729872),
 ('jerky.rcp', 60.19579447299453),
 ('chili.txt', 59.879415684550295),
 ('roadpizz.txt', 50.9010430699485),
 ('shuimai.txt', 36.562899643132155),
 ('pizzawho.hum', 29.719809915989003),
 ('bread.rcp', 27.235491576474963)]

Term Frequency

In [ ]:
tf_idf_scores_query = {}
for doc in dict_file_nums.values():
  sc = tf_idf_score(query,term_document_count_term_frequency_df,doc)
  tf_idf_scores_query[doc]=sc
tf_idf_scores_query_sorted = sorted(tf_idf_scores_query.items(), key=lambda x: x[1], reverse=True)
print("Documents Matched using Term Frequency:\n")
tf_idf_scores_query_sorted[:10]

Documents Matched using Term Frequency:



[('pasta001.sal', 0.1057976527404703),
 ('garlpast.vgn', 0.0969138803729499),
 ('roadpizz.txt', 0.08540443468112163),
 ('fish.rec', 0.07097770919968628),
 ('fbipizza.txt', 0.06976488347948832),
 ('oranchic.pol', 0.04851947460204402),
 ('strattma.txt', 0.04416006826026164),
 ('buffwing.pol', 0.039123716598520535),
 ('venganza.txt', 0.03612975001752629),
 ('capital.txt', 0.03526951787425185)]

Log Normalization

In [ ]:
tf_idf_scores_query = {}
for doc in dict_file_nums.values():
  sc = tf_idf_score(query,term_document_count_log_normalization_df,doc)
  tf_idf_scores_query[doc]=sc
tf_idf_scores_query_sorted = sorted(tf_idf_scores_query.items(), key=lambda x: x[1], reverse=True)
print("Documents Matched using Log Normalization:\n")
tf_idf_scores_query_sorted[:10]

Documents Matched using Log Normalization:



[('appetiz.rcp', 13.194647969425413),
 ('vegan.rcp', 11.862101959901475),
 ('penndtch', 10.299416766393662),
 ('bread.rcp', 7.367469559273125),
 ('chili.txt', 7.220851808013785),
 ('jerky.rcp', 6.758764421366658),
 ('shuimai.txt', 6.322109435008565),
 ('pizzawho.hum', 5.9852168953708915),
 ('top10.txt', 5.52321032775934),
 ('fajitas.rcp', 5.498819181722448)]

Double Normalization

In [ ]:
tf_idf_scores_query = {}
for doc in dict_file_nums.values():
  sc = tf_idf_score(query,term_document_count_double_normalization_df,doc)
  tf_idf_scores_query[doc]=sc
tf_idf_scores_query_sorted = sorted(tf_idf_scores_query.items(), key=lambda x: x[1], reverse=True)
print("Documents Matched using Double Normalization:\n")
tf_idf_scores_query_sorted[:10]

Documents Matched using Double Normalization:



[('pasta001.sal', 3.3031654409718305),
 ('garlpast.vgn', 3.29872355478807),
 ('roadpizz.txt', 3.292968831942156),
 ('fish.rec', 3.2857554692014386),
 ('fbipizza.txt', 3.2851490563413397),
 ('oranchic.pol', 3.274526351902617),
 ('strattma.txt', 3.272346648731726),
 ('buffwing.pol', 3.2698284729008553),
 ('venganza.txt', 3.2683314896103584),
 ('capital.txt', 3.267901373538721)]